In [1]:
# True : 문서 임베딩을 피클 파일에서 읽음, False : 임베딩을 새로함
is_use_doc_embeddings_from_pickle = True

# True : 문서로부터 생성된 질문의 임베딩을 피클 파일에서 읽음, False : 임베딩을 새로함
is_use_qfc_embeddings_from_pickle = True

# 문서 임베딩의 피클 파일명
doc_embeddings_pickle_filename = 'embeddings_text-embedding-3-large_dim3072.pkl'

# 문서로부터 생성된 질문 임베딩의 피클 파일명
# "qfc" == "questions_from_contents"
qfc_embeddings_pickle_filename = 'qfc_embeddings_text-embedding-3-large_dim3072.pkl'

In [2]:
import os
from dotenv import load_dotenv
load_dotenv()

True

In [3]:
 # 색인 대상 문서 및 평가 데이터 다운로드
 #!wget https://aistages-api-public-prod.s3.amazonaws.com/app/Competitions/000291/data/data.tar.gz
 #!tar -xzvf data.tar.gz

## 환경 설정
검색엔진을 위한 Elasitcsearch, 임베딩 생성을 위한 sentence transformers, LLM 사용을 위한 openai client 설치가 필요합니다.

In [4]:
# GPU를 사용하는 버전의 Faiss Python 패키지 설치
#!pip install faiss-gpu

# OpenAI Python 패키지 설치
#!pip install openai==1.7.2

# 임베딩 생성을 위한 벡터 인코더 설치
#!pip install sentence-transformers==2.2.2

In [5]:
import os
import json
import faiss
import numpy as np

In [6]:
from openai import OpenAI
import traceback

# OpenAI API 키를 환경변수에 설정
os.environ["OPENAI_API_KEY"] = os.getenv('OPENAI_API_KEY')
#os.environ["OPENAI_API_KEY"] = "Your API Key"

client = OpenAI()
# 사용할 모델을 설정(여기서는 gpt-3.5-turbo-1106 모델 사용)
llm_model = "gpt-3.5-turbo-1106"
#llm_model = "gpt-4o-2024-08-06"

In [7]:
def get_embedding(text, model="text-embedding-3-large"):
   return client.embeddings.create(input=[text], model=model).data[0].embedding


def texts_to_tensor(texts, model="text-embedding-3-large"):
    embeddings = [get_embedding(text, model) for text in texts]
    return embeddings


# 주어진 문서의 리스트에서 배치 단위로 임베딩 생성
def get_embeddings_in_batches(datas, key, batch_size=100):
    batch_embeddings = []
    for i in range(0, len(datas), batch_size):
        batch = datas[i:i + batch_size]
        contents = [data[key] for data in batch]
        
        #embeddings = get_embedding(contents)
        embeddings = texts_to_tensor(contents)
        
        batch_embeddings.extend(embeddings)
        print(f'batch {i}')
        
    return batch_embeddings

In [8]:
with open("../../data/documents.jsonl") as f:
    docs = [json.loads(line) for line in f]

with open("./questions_from_contents.jsonl") as f:
    qfcs = [json.loads(line) for line in f]

In [9]:
import pickle

if not is_use_doc_embeddings_from_pickle:
    doc_embeddings = get_embeddings_in_batches(docs, "content")
    
    # 나중을 위해 임베딩을 피클 파일로 저장.
    with open(doc_embeddings_pickle_filename, 'wb') as file:
        pickle.dump(doc_embeddings, file)
else:
    # 피클 파일로부터 embeddings 리스트 복원
    with open(doc_embeddings_pickle_filename, 'rb') as file:
        doc_embeddings = pickle.load(file)
        

if not is_use_qfc_embeddings_from_pickle:
    qfc_embeddings = get_embeddings_in_batches(qfcs, "question")
    
    # 나중을 위해 임베딩을 피클 파일로 저장.
    with open(qfc_embeddings_pickle_filename, 'wb') as file:
        pickle.dump(qfc_embeddings, file)
else:
    # 피클 파일로부터 embeddings 리스트 복원
    with open(qfc_embeddings_pickle_filename, 'rb') as file:
        qfc_embeddings = pickle.load(file)

In [10]:
print(f'doc embedding dimension : {len(doc_embeddings[0])}')
print(f'doc embeddings type : {type(doc_embeddings)}')
print(f'doc embeddings length : {len(doc_embeddings)}')
print(f'doc embeddings[0] : {doc_embeddings[0]}')
print()

print(f'qfc embedding dimension : {len(qfc_embeddings[0])}')
print(f'qfc embeddings type : {type(qfc_embeddings)}')
print(f'qfc embeddings length : {len(qfc_embeddings)}')
print(f'qfc embeddings[0] : {qfc_embeddings[0]}')

doc embedding dimension : 3072
doc embeddings type : <class 'list'>
doc embeddings length : 4272
doc embeddings[0] : [0.03257926180958748, -0.008541478775441647, -0.00882707629352808, -0.01854267716407776, -0.011275810189545155, 0.015464572235941887, -0.016226164996623993, -0.019177338108420372, 0.011053678579628468, -0.07544003427028656, 0.036768026649951935, -0.008287614211440086, 0.014840489253401756, -0.00774815259501338, 0.0235670767724514, -0.011244077235460281, 0.01890231855213642, -0.007134647108614445, 0.04366467520594597, 0.0019330715294927359, -0.001348654506728053, -0.03587950021028519, 0.004318338818848133, 0.0014755867887288332, -0.013698099181056023, -0.005405195988714695, 0.014353915117681026, 0.01808783784508705, 0.00666922889649868, -0.039116270840168, -0.029025161638855934, 0.0273327324539423, -0.02068994753062725, -0.002837463514879346, -0.031986914575099945, -0.024476757273077965, 0.01512608677148819, 0.00987955555319786, 0.0035514570772647858, 0.02659229375422001,

In [11]:
doc_embedding_dims = len(doc_embeddings[0])
index_docs = faiss.IndexFlatL2(doc_embedding_dims)
index_docs.add(np.array(doc_embeddings).astype('float32'))

qfc_embedding_dims = len(qfc_embeddings[0])
index_qfcs = faiss.IndexFlatL2(qfc_embedding_dims)
index_qfcs.add(np.array(qfc_embeddings).astype('float32'))

In [12]:
# Vector 유사도를 이용한 검색
def dense_retrieve(faiss_obj, faiss_index_name, query_str, size):
    # 벡터 유사도 검색에 사용할 쿼리 임베딩 가져오기
    query_emb = get_embedding(query_str)
    query_emb = np.array([query_emb]).astype('float32')

    # Faiss 인덱스 생성시 IndexFlatL2() 함수를 사용했으므로 scores 의 값이 작을수록 관련성이 높음!
    # (L2 는 유클리드 거리를 의미하므로)
    scores, offsets = faiss_obj.search(query_emb, size)

    ret = []
    
    if faiss_index_name == "docs":
        ret = [
                {
                    # mandatory
                    "score": scores[0][i].astype(float),    # 이렇게 타입을 바꾸지 않으면 나중에 json dump 시 에러 발생함.
                    "doc": docs[ offsets[0][i] ],
                }
                for i in range(len(scores[0]))
            ]
    elif faiss_index_name == "qfcs":
        ret = [
                {
                    # mandatory
                    "score": scores[0][i].astype(float),    # 이렇게 타입을 바꾸지 않으면 나중에 json dump 시 에러 발생함.
                    "doc": docs[ qfcs[offsets[0][i]]['docOffset'] ],
                    
                    # optional
                    "question_from_content": qfcs[ offsets[0][i] ]['question'],
                }
                for i in range(len(scores[0]))
            ]
    else:
        assert False, "wrong faiss index name.."
    
    return ret

In [13]:
# 검색엔진에 색인이 잘 되었는지 테스트하기 위한 질의
query_str = "나무의 분류에 대해 조사해 보기 위한 방법은?"

ret = dense_retrieve(index_docs, "docs", query_str, 5)
print(ret)
print()

ret = dense_retrieve(index_qfcs, "qfcs", query_str, 5)
print(ret)

[{'score': 0.7371037602424622, 'doc': {'docid': 'c63b9e3a-716f-423a-9c9b-0bcaa1b9f35d', 'src': 'ko_ai2_arc__ARC_Challenge__test', 'content': '한 학생이 다양한 종류의 나무를 조사하고 있습니다. 이 학생은 성장 속도, 온도 범위, 크기가 비슷한 두 나무를 발견했습니다. 그러나 이 두 나무의 잎과 꽃은 서로 다릅니다. 이러한 특징을 고려하면, 이 나무들은 대체로 같은 속에 속해 있을 것으로 추측됩니다. 같은 속에 속한 나무들은 종류별로 유사한 특징을 가지고 있으며, 이는 생물 분류학에서 중요한 기준 중 하나입니다. 따라서 이 학생의 조사 결과는 나무의 분류와 관련된 중요한 정보를 제공할 수 있습니다. 이러한 조사는 나무의 성장과 생태에 대한 이해를 높이는 데 도움이 될 것입니다.'}}, {'score': 1.106291651725769, 'doc': {'docid': '4f11bc9b-1b9c-47f1-8600-bcdf78db5b92', 'src': 'ko_ai2_arc__ARC_Challenge__test', 'content': '메인주의 발삼전나무는 바늘잎 길이가 비슷합니다. 이는 씨앗 내부의 유전 정보 때문입니다. 발삼전나무의 씨앗은 유전 정보를 가지고 있으며, 이 정보는 바늘잎의 길이에 영향을 미칩니다. 따라서, 발삼전나무의 씨앗이 비슷한 유전 정보를 가지고 있기 때문에 바늘잎의 길이도 비슷하게 나타납니다. 이러한 특성은 발삼전나무를 식별하는데 도움을 줄 수 있습니다.'}}, {'score': 1.1346917152404785, 'doc': {'docid': '9712bdf6-9419-4953-a8f1-8a4015dee986', 'src': 'ko_ai2_arc__ARC_Challenge__train', 'content': '생물학에서 일부 생물체의 분류 방법이 변경되었습니다. 이제 생물체를 재분류하는 데에는 구조보다는 분자 수준에서의 조사가 사

## RAG 구현

준비된 검색엔진과 LLM을 활용하셔 대화형 RAG 구현

In [14]:
# RAG 구현에 필요한 Question Answering을 위한 LLM  프롬프트
persona_qa = """
## Role: 과학 상식 전문가

## Instructions
- 사용자의 이전 메시지 정보 및 주어진 Reference 정보를 활용하여 간결하게 답변을 생성한다.
- 주어진 검색 결과 정보로 대답할 수 없는 경우는 정보가 부족해서 답을 할 수 없다고 대답한다.
- 한국어로 답변을 생성한다.
"""

# RAG 구현에 필요한 질의 분석 및 검색 이외의 일반 질의 대응을 위한 LLM 프롬프트
persona_function_calling = """
## Role: 과학 상식 전문가

## Instruction
- 사용자가 대화를 통해 과학 지식에 관한 주제로 질문하면 search api를 호출할 수 있어야 한다.
- search api를 호출할 때, 사용자의 대화가 멀티턴이 아니라면, 사용자의 대화 내용을 그대로 standalone_query 에 대입한다.
- 과학 상식과 관련되지 않은 나머지 대화 메시지에는 적절한 대답을 생성한다.
"""

# Function calling에 사용할 함수 정의
tools = [
    {
        "type": "function",
        "function": {
            "name": "search",
            "description": "search relevant documents",
            "parameters": {
                "properties": {
                    "standalone_query": {
                        "type": "string",
                        "description": "Final query suitable for use in search from the user messages history."
                    }
                },
                "required": ["standalone_query"],
                "type": "object"
            }
        }
    },
]

In [15]:
# LLM과 검색엔진을 활용한 RAG 구현
def answer_question(messages):
    # 함수 출력 초기화
    response = {"standalone_query": "", "topk": [], "references": [], "answer": ""}

    # 질의 분석 및 검색 이외의 질의 대응을 위한 LLM 활용
    msg = [{"role": "system", "content": persona_function_calling}] + messages
    try:
        result = client.chat.completions.create(
            model=llm_model,
            messages=msg,
            tools=tools,
            #tool_choice={"type": "function", "function": {"name": "search"}},
            temperature=0,
            seed=1,
            timeout=10
        )
    except Exception as e:
        traceback.print_exc()
        return response

    # 검색이 필요한 경우 검색 호출후 결과를 활용하여 답변 생성
    if result.choices[0].message.tool_calls:
        tool_call = result.choices[0].message.tool_calls[0]
        function_args = json.loads(tool_call.function.arguments)
        standalone_query = function_args.get("standalone_query")
        response["standalone_query"] = standalone_query

        search_result_docs = dense_retrieve(index_docs, "docs", standalone_query, 50)
        search_result_qfcs = dense_retrieve(index_qfcs, "qfcs", standalone_query, 50)
        
        hits_merged_list = search_result_docs + search_result_qfcs
        hits_merged_list.sort(key=lambda x: x["score"])
        
        print(f'before removing dup result count: {len(hits_merged_list)}')
        
        # 동일한 문서 제거
        dup_removed_result_dic = {}
        for rst in hits_merged_list:
            key = rst['doc']['docid']
            
            if key in dup_removed_result_dic:
                continue
            
            dup_removed_result_dic[key] = rst

        for rst in dup_removed_result_dic.values():
            log = f"score: {rst['score']}"
            
            if 'question_from_content' in rst:
                log += f", qfc: {rst['question_from_content']}"
            else:
                log += f", content: {rst['doc']['content']}"
            
            print(log)
        
        print(f'after removing dup result count: {len(dup_removed_result_dic)}')
                
        retrieved_context = []
        for i, rst in enumerate(dup_removed_result_dic.values()):
            if i >= 3:
                break   # 최대 3개까지만..
            
            retrieved_context.append(rst["doc"]["content"])
            
            response["topk"].append(rst["doc"]["docid"])
            response["references"].append({"score": rst["score"], "content": rst["doc"]["content"]})

        content = json.dumps(retrieved_context)
        messages.append({"role": "assistant", "content": content})
        msg = [{"role": "system", "content": persona_qa}] + messages
        try:
            qaresult = client.chat.completions.create(
                    model=llm_model,
                    messages=msg,
                    temperature=0,
                    seed=1,
                    timeout=30
                )
        except Exception as e:
            traceback.print_exc()
            return response
        response["answer"] = qaresult.choices[0].message.content

    # 검색이 필요하지 않은 경우 바로 답변 생성
    else:
        response["answer"] = result.choices[0].message.content

    return response

In [19]:
# 평가를 위한 파일을 읽어서 각 평가 데이터에 대해서 결과 추출후 파일에 저장
def eval_rag(eval_filename, output_filename):
    with open(eval_filename) as f, open(output_filename, "w") as of:
        idx = 0
        for line in f:
            # if idx > 1:
            #     break
            j = json.loads(line)
            print(f'Test {idx}\nQuestion: {j["msg"]}')
            response = answer_question(j["msg"])
            print(f'Answer: {response["answer"]}\n')

            # 대회 score 계산은 topk 정보를 사용, answer 정보는 LLM을 통한 자동평가시 활용
            output = {"eval_id": j["eval_id"], "standalone_query": response["standalone_query"], "topk": response["topk"], "answer": response["answer"], "references": response["references"]}
            of.write(f'{json.dumps(output, ensure_ascii=False)}\n')
            idx += 1


In [20]:
# 평가 데이터에 대해서 결과 생성 - 파일 포맷은 jsonl이지만 파일명은 csv 사용
submission_filename = "submission_011.csv"

eval_rag("../../data/eval.jsonl", submission_filename)

Test 0
Question: [{'role': 'user', 'content': '나무의 분류에 대해 조사해 보기 위한 방법은?'}]
before removing dup result count: 100
score: 0.5363765358924866, qfc: 학생의 조사가 나무의 분류에 어떻게 기여할 수 있나요?
score: 0.8972891569137573, qfc: 나무의 고유 주파수를 측정하는 방법은 무엇인가요?
score: 0.9065408706665039, qfc: 나무를 지속적으로 활용하기 위한 방법에는 무엇이 있나요?
score: 0.9299575686454773, qfc: 발삼전나무의 유전 정보는 어떻게 연구되고 있나요?
score: 0.9384165406227112, qfc: 나무의 재생 가능성을 높이기 위한 기술이나 방법에는 어떤 것들이 있나요?
score: 0.9498440027236938, qfc: 나무의 생명 주기에서 성장은 어떤 과정을 포함하나요?
score: 0.9579006433486938, qfc: 나무는 어떤 물질로 구성되어 있나요?
score: 0.9586454033851624, qfc: 새로 발견된 생물체를 분류하기 위한 조사 과정은 어떻게 진행되나요?
score: 0.9637182354927063, qfc: 생물체의 재분류에 사용되는 분자 수준의 조사 방법에는 어떤 것들이 있나요?
score: 0.9637532830238342, qfc: 나무는 어떤 형태로 열 생산에 이용되나요?
score: 0.9893567562103271, qfc: 참나무의 건강과 번성은 어떻게 측정할 수 있나요?
score: 1.0021436214447021, qfc: 나무를 심고 성장시키는 것 외에 어떤 관리가 필요한가요?
score: 1.0229276418685913, qfc: 떡갈나무의 잎의 길이와 너비를 정확하게 측정하려면 어떻게 해야 하나요?
score: 1.0558061599731445, qfc: 나무가 산업 분야에서 어떻게 활용되는지 예

#Reference

## Required Package

openai==1.7.2 <br>
elasticsearch==8.8.0 <br>
sentence_transformers==2.2.2 <br>



## 콘텐츠 라이선스

저작권 : <font color='blue'> <b> ©2023 by Upstage X fastcampus Co., Ltd. All rights reserved.</font></b>

<font color='red'><b>WARNING</font> : 본 교육 콘텐츠의 지식재산권은 업스테이지 및 패스트캠퍼스에 귀속됩니다. 본 콘텐츠를 어떠한 경로로든 외부로 유출 및 수정하는 행위를 엄격히 금합니다. </b>